# Conway's game of life cellular automaton

Wikipedia [1] says:

> The Game of Life, also known simply as Life, is a cellular automaton
> devised by the British mathematician John Horton Conway in 1970.

> The 'game' is a zero-player game, meaning that its evolution is
> determined by its initial state, requiring no further input. One
> interacts with the Game of Life by creating an initial configuration
> and observing how it evolves.

[1] http://en.wikipedia.org/wiki/Conway's_Game_of_Life


## Imports and setup

In [ ]:
%matplotlib notebook
import time
import numpy as np
import matplotlib.pyplot as plt

plt.close('all')

np.set_printoptions(threshold=1000)

## Transition functions

Rules (slightly modified for computer)

The universe of the Game of Life is a rectangular (originally infinite)
two-dimensional orthogonal grid of square cells, each of which is in one
of two possible states, live or dead. Every cell interacts with its
eight neighbours, which are the cells that are directly horizontally,
vertically, or diagonally adjacent. At each step in time, the following
transitions occur:

1. Any live cell with fewer than two live neighbours dies, as if caused by under-population.

2. Any live cell with more than three live neighbours dies, as if by overcrowding.

3. Any live cell with two or three live neighbours lives on to the next generation.

4. Any dead cell with exactly three live neighbours becomes a live cell, as if by reproduction.

The initial pattern constitutes the seed of the system. The first
generation is created by applying the above rules simultaneously to
every cell in the seed - births and deaths occur simultaneously, and the
discrete moment at which this happens is sometimes called a tick (in
other words, each generation is a pure function of the preceding
one). The rules continue to be applied repeatedly to create further
generations.

As the grid is finite, boundary conditions need to be applied. Two
basic possibilities are:

- border strip of death
- periodic conditions

There are three example implementations here:

- make_life_step_naive() (using for loops)
- make_life_step_cool() (using stride tricks)
- make_life_step() (using fancy indexing)

Other ways are possible, of course, e.g. using numpy.roll().


In [ ]:
def make_life_step_naive(state, bc_type='death'):
    """
    The transition function, that performs single step of the Game of
    Life. A naive implementation using loops, 'death' boundary condition
    type only.
    """
    new_state = state.copy()

    if bc_type == 'death':
        active = state[1:-1, 1:-1]

        for ir, row in enumerate(active):
            for ic, val in enumerate(row):
                nn = np.sum(state[ir:ir+3, ic:ic+3]) - val
                # print(ir, ic, nn)
                if (nn < 2) or (nn > 3):
                    new_state[ir+1, ic+1] = 0

                if nn == 3:
                    new_state[ir+1, ic+1] = 1

    else:
        raise NotImplementedError

    return new_state

In [ ]:
def make_life_step_tricks(state, bc_type='death'):
    """
    The transition function, that performs single step of the Game of
    Life. An implementation using stride tricks, 'death' boundary
    condition type only.
    """
    from numpy.lib import stride_tricks

    new_state = state.copy()

    s0, s1 = state.strides
    n_row, n_col = state.shape

    if bc_type == 'death':
        active = new_state[1:-1, 1:-1]

        magic = stride_tricks.as_strided(state,
                                         shape=(n_row - 2, n_col - 2, 3, 3),
                                         strides=(s0, s1, s0, s1))

        nn = magic.sum(axis=2).sum(axis=2) - active
        # nn = magic.sum(axis=(2, 3)) - active
        # nn = magic.sum(axis=(2, 3))
        # nn -= active

        i_dead = np.where((nn < 2) | (nn > 3))
        i_live = np.where((nn == 3))

        active[i_dead] = 0
        active[i_live] = 1

    else:
        raise NotImplementedError

    return new_state

In [ ]:
def make_life_step(state, bc_type='death'):
    """
    The transition function, that performs single step of the Game of
    Life. Reasonable implementation using fancy indexing, both 'death'
    and 'periodic' boundary condition types.
    """
    n_row, n_col = state.shape

    # Get neighbour indices for all cells according to boundary conditions.
    if bc_type == 'death':
        ir0 = np.arange(0, n_row - 2)[:, None]
        ir1 = ir0 + 1
        ir2 = ir1 + 1

        ic0 = np.arange(0, n_col - 2)
        ic1 = ic0 + 1
        ic2 = ic1 + 1

        irs = slice(1, -1)
        ics = slice(1, -1)

    elif bc_type == 'periodic':
        ir1 = np.arange(0, n_row)[:, None]
        ir0 = np.roll(ir1, 1)
        ir2 = np.roll(ir1, -1)

        ic1 = np.arange(0, n_col)
        ic0 = np.roll(ic1, 1)
        ic2 = np.roll(ic1, -1)

        irs = slice(0, None)
        ics = slice(0, None)

    else:
        raise ValueError('unknown BC type! (%s)' % bc_type)

    # Count neighbours.
    nn = state[ir0, ic0] + state[ir0, ic1] + state[ir0, ic2] + \
         state[ir1, ic0] +               0 + state[ir1, ic2] + \
         state[ir2, ic0] + state[ir2, ic1] + state[ir2, ic2]

    new_state = state.copy()

    # Make a view to the active part of the grid.
    active = new_state[irs, ics]

    i_dead = np.where((nn < 2) | (nn > 3))
    i_live = np.where((nn == 3))

    active[i_dead] = 0
    active[i_live] = 1

    return new_state

In [ ]:
def make_life_step_convolve(state, bc_type='death'):
    """
    The transition function, that performs single step of the Game of
    Life. Scipy-based implementation using convolve2d(), both 'death'
    and 'periodic' boundary condition types.
    """
    from scipy.signal import convolve2d

    n_row, n_col = state.shape

    # Count neighbours and Get neighbour indices for all cells according to
    # boundary conditions.
    m = np.array([[1, 1, 1], [1, 0, 1], [1, 1, 1]])
    if bc_type == 'death':
        nn = convolve2d(state, m, mode='valid', boundary='pad')

        irs = slice(1, -1)
        ics = slice(1, -1)

    elif bc_type == 'periodic':
        nn = convolve2d(state, m, mode='same', boundary='wrap')

        irs = slice(0, None)
        ics = slice(0, None)

    else:
        raise ValueError('unknown BC type! (%s)' % bc_type)

    new_state = state.copy()

    # Make a view to the active part of the grid.
    active = new_state[irs, ics]

    i_dead = np.where((nn < 2) | (nn > 3))
    i_live = np.where((nn == 3))

    active[i_dead] = 0
    active[i_live] = 1

    return new_state

## Draw state

In [ ]:
def plot_life_animation(image, state, bc_type, pause=0.0):
    """
    Animate the Game of Life. Debug (blocking) version.
    """
    fig = plt.gcf()

    label = plt.title('iteration 0')

    ii = 0
    while 1:
        # t0 = time.clock()
        state = make_life_step_convolve(state, bc_type)
        # print(time.clock() - t0)

        image.set_data(state)

        ii += 1
        label.set_text('iteration %d' % ii)

        fig.canvas.draw()
        time.sleep(pause)
        yield True

## Simulation parameters

In [ ]:
# Grid dimensions.
n_row = 15
n_col = 20

# Boundary conditions ('death' or 'periodic').
bc_type = 'death'
# bc_type = 'periodic'

# Slow down animation.
pause = 0.1

## Initialization

In [ ]:
state = np.round(np.random.rand(n_row, n_col)).astype(np.int8)

if bc_type == 'death':
    state[0, :] = 0
    state[-1, :] = 0
    state[:, 0] = 0
    state[:, -1] = 0

image = plt.spy(state)

## Animate the game of life

In [ ]:
plt.figure()

image = plt.spy(state)

for ii, _ in enumerate(plot_life_animation(image, state, bc_type, pause)):
    # if ii > 20: break
    pass

In [ ]:
%timeit make_life_step(state, bc_type)

In [ ]:
%timeit make_life_step_naive(state, bc_type)

In [ ]:
%timeit make_life_step_tricks(state, bc_type)

In [ ]:
%timeit make_life_step_convolve(state, bc_type)

In [ ]:
(make_life_step_naive(state, bc_type) == make_life_step(state, bc_type)).all()

In [ ]:
(make_life_step_convolve(state, bc_type) == make_life_step(state, bc_type)).all()

In [ ]:
(make_life_step_tricks(state, bc_type) == make_life_step(state, bc_type)).all()

In [ ]:
make_life_step_naive(state, bc_type)

In [ ]:
make_life_step(state, bc_type)

In [ ]:
state